# Comparing the two AORC forcing data versions (AWS vs. Cheyenne)

The purpose of this Jupyter notebook is to explore the differences  between the two AORC (Analysis of Record for 
Calibration) forcing data versions (old vs. new version). We obtained the old version of AORC data from Amazon S3 Bucket 
(https://noaa-nwm-retrospective-2-1-pds.s3.amazonaws.com/index.html#forcing/), while the new version (v 1.1) dataset retrieved from Cheyenne supercomputer (https://arc.ucar.edu/knowledge_base/70549542).
1. Exploring the metadata for each individual AORC dataset.
2. Subsetting the AORC using a shapefile extents (bounds).
3.Comparing between the two AORC versions (AWS vs. Cheyenne).

## Case Study

This map layout represents the Logan River Watershed in Utah. 

<center><img src="statics//Layout.jpg" width=400 height=300 /></center>

<div class="alert alert-block alert-success">
<b>Import all libraries needed to run this Jupyter notebook</b> 

</div>

In [1]:
# Imports

import os
import subprocess
import netCDF4 as nc
import xarray as xr
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import pyproj
import fiona
from shapely.geometry import shape

## Exploring the AORC datasets metadata with detailed infromation about dimensions, varibales, and geographic reference.

<div class="alert alert-block alert-success">
<b>Metadata for each AORC dataset (AWS (old version) vs. Cheyenne (new version - v 1.1))</b> 

</div>

In [2]:
## Metadata of each dataset

aorc_aws="./AORC_AWS"   # directory of AORC datasets obtained from AWS
aorc_ch="./AORC_Cheyenne"  # directory of AORC datasets obtained from Cheyenne supercomputer

aorc_aws_path= aorc_aws + "/2016010100.LDASIN_DOMAIN1" # path of one AORC dataset from AWS (old version)
aorc_ch_path= aorc_ch + "/201601010000.LDASIN_DOMAIN1" # path of one AORC datset from Cheyenne super computer (new version v 1.1)

meta_data_aws = subprocess.run(["ncdump", "-h", aorc_aws_path])
meta_data_ch = subprocess.run(["ncdump", "-h", aorc_ch_path])
print(meta_data_aws)
print(meta_data_ch)

netcdf \2016010100 {
dimensions:
	DateStrLen = 20 ;
	Time = 1 ;
	south_north = 3840 ;
	west_east = 4608 ;
variables:
	char Times(DateStrLen) ;
	double valid_time(Time) ;
		valid_time:calendar = "standard" ;
		valid_time:units = "seconds since 1970-01-01 00:00:00" ;
	float RAINRATE(Time, south_north, west_east) ;
		RAINRATE:description = "RAINRATE" ;
		RAINRATE:missing_value = 9.999e+20f ;
		RAINRATE:remap = "remapped via ESMF_regrid_with_weights: Bilinear" ;
		RAINRATE:initial_time = "12/31/2015 (23:00)" ;
		RAINRATE:forecast_time_units = "hours" ;
		RAINRATE:forecast_time = 1 ;
		RAINRATE:statistical_process_duration = "initial time to forecast time" ;
		RAINRATE:type_of_statistical_processing = "Accumulation" ;
		RAINRATE:level = 0.f ;
		RAINRATE:level_type = "Ground or water surface" ;
		RAINRATE:parameter_template_discipline_category_number = 8, 0, 1, 8 ;
		RAINRATE:parameter_discipline_and_category = "Meteorological products, Moisture" ;
		RAINRATE:grid_type = "Latitude/longitude"

<div class="alert alert-block alert-success">
<b> AORC dimension values</b> 

</div>

In [3]:
ds_aws=nc.Dataset(aorc_aws_path)
ds_ch=nc.Dataset(aorc_ch_path)

print("AORC_AWS dimensions values")
for d in ds_aws.dimensions.values():
    print(d)

print("AORC_Ch dimensions values")
for d in ds_ch.dimensions.values():
    print(d)

AORC_AWS dimensions values
<class 'netCDF4._netCDF4.Dimension'>: name = 'DateStrLen', size = 20
<class 'netCDF4._netCDF4.Dimension'>: name = 'Time', size = 1
<class 'netCDF4._netCDF4.Dimension'>: name = 'south_north', size = 3840
<class 'netCDF4._netCDF4.Dimension'>: name = 'west_east', size = 4608
AORC_Ch dimensions values
<class 'netCDF4._netCDF4.Dimension'> (unlimited): name = 'time', size = 1
<class 'netCDF4._netCDF4.Dimension'>: name = 'y', size = 3840
<class 'netCDF4._netCDF4.Dimension'>: name = 'x', size = 4608
<class 'netCDF4._netCDF4.Dimension'>: name = 'reference_time', size = 1


<div class="alert alert-block alert-success">
<b> AORC variables</b> 

</div>

In [4]:
print("AORC_AWS variables")
for var in ds_aws.variables:
    print(var)

print("AORC_Ch variables")
for var in ds_ch.variables:
    print(var)

AORC_AWS variables
Times
valid_time
RAINRATE
T2D
Q2D
U2D
V2D
PSFC
SWDOWN
LWDOWN
AORC_Ch variables
time
reference_time
x
y
crs
U2D
V2D
LWDOWN
RAINRATE
T2D
Q2D
PSFC
SWDOWN
LQFRAC


<div class="alert alert-block alert-success">
<b> AORC variable values (providing detailed information about each individual variable)</b> 

</div>

In [5]:
print("AORC_AWS variables values")
for v in ds_aws.variables.values():
    print(v)

print("AORC_Ch variables values")
for v in ds_ch.variables.values():
    print(v)

AORC_AWS variables values
<class 'netCDF4._netCDF4.Variable'>
|S1 Times(DateStrLen)
unlimited dimensions: 
current shape = (20,)
filling on, default _FillValue of   used
<class 'netCDF4._netCDF4.Variable'>
float64 valid_time(Time)
    calendar: standard
    units: seconds since 1970-01-01 00:00:00
unlimited dimensions: 
current shape = (1,)
filling on, default _FillValue of 9.969209968386869e+36 used
<class 'netCDF4._netCDF4.Variable'>
float32 RAINRATE(Time, south_north, west_east)
    description: RAINRATE
    missing_value: 9.999e+20
    remap: remapped via ESMF_regrid_with_weights: Bilinear
    initial_time: 12/31/2015 (23:00)
    forecast_time_units: hours
    forecast_time: 1
    statistical_process_duration: initial time to forecast time
    type_of_statistical_processing: Accumulation
    level: 0.0
    level_type: Ground or water surface
    parameter_template_discipline_category_number: [8 0 1 8]
    parameter_discipline_and_category: Meteorological products, Moisture
    grid

<div class="alert alert-block alert-success">
<b> The coordinate reference system (CRS) used for each AORC dataset</b> 

</div>

In [6]:
# The new version of AORC v 1.1 is georeferenced using the Lambert Conformal Conic (lcc)

# Geographic reference used for AORC data from AWS (old version)
# ds_aws.variables['crs'].esri_pe_string

# Geographic reference used for AORC data from Cheyenne supercomputer (new  version v 1.1)
ds_ch.variables['crs'].esri_pe_string

'PROJCS["Lambert_Conformal_Conic",GEOGCS["GCS_Sphere",DATUM["D_Sphere",SPHEROID["Sphere",6370000.0,0.0]],PRIMEM["Greenwich",0.0],UNIT["Degree",0.0174532925199433]],PROJECTION["Lambert_Conformal_Conic_2SP"],PARAMETER["false_easting",0.0],PARAMETER["false_northing",0.0],PARAMETER["central_meridian",-97.0],PARAMETER["standard_parallel_1",30.0],PARAMETER["standard_parallel_2",60.0],PARAMETER["latitude_of_origin",40.0],UNIT["Meter",1.0]];-35691800 -29075200 10000;-100000 10000;-100000 10000;0.001;0.001;0.001;IsHighPrecision'

## Subsetting AORC dataset using a shapefile (extents)

<div class="alert alert-block alert-success">
<b> Read the extends (bounds) of the shapefile to subset AORC data</b> 

</div>

In [7]:
## path of the shapefile
input_dir="./"  
# shape_file="Logan_River_Basin_Shapefile/Logan_River_Watershed_lcc.shp"
shape_file="subwatershd_test/subwatersh_test.shp"
sf_path = os.path.join(input_dir, shape_file)

# open the shapefile to read the extends (bounds) of the shapefile geometry
sf = fiona.open(sf_path)  # open the shapefile
sf = sf.next()
sh_bounds = shape(sf['geometry']).bounds # read the geometry extents (bounds)

## extents (bounds) of the shapefile used in this use case
top= sh_bounds[3]  # top bound
bottom= sh_bounds[1] # bottom bound
left = sh_bounds[0] # left bound
right = sh_bounds[2]

## print all extents (bounds) that include top, bottom, left and right
print("Extent")
print("Top: {}, Bottom: {}, Left: {}, Right:{}".format(top, bottom, left, right))

Extent
Top: 301050.07030000165, Bottom: 292307.27760000154, Left: -1181161.8989000022, Right:-1167824.1692000031


/tmp/ipykernel_611/2552138311.py:9: FionaDeprecationWarning: Collection.__next__() is buggy and will be removed in Fiona 2.0. Switch to `next(iter(collection))`.
  sf = sf.next()


In [10]:
input_dir="./"
nwm_file="201601010000.CHRTOUT_DOMAIN1.comp"
nwm_file="201801010300.LDASOUT_DOMAIN1.comp"

nwm_example = nc.Dataset(os.path.join(input_dir, nwm_file))

pr = pyproj.Proj(nwm_example.variables['crs'].esri_pe_string)

pr

# Open the example NWM file and read  X and Y indices of all grids from one NWM file
# nc_NWM = xr.open_dataset(os.path.join(input_dir, nwm_file))
# X_NWM = nc_NWM.coords['x']
# Y_NWM = nc_NWM.coords['y']

<Other Coordinate Operation Transformer: lcc>
Description: PROJ-based coordinate operation
Area of Use:
- undefined

<div class="alert alert-block alert-success">
<b> Specify the indices to be used for subsetting the AORC datasets</b> 

</div>

In [11]:
# the path for any CONUS nwm data
input_dir="./"
nwm_file="201601010000.LDASOUT_DOMAIN1.comp"
# nwm_file="201801010300.LDASOUT_DOMAIN1.comp"

nc_NWM = xr.open_dataset(os.path.join(input_dir, nwm_file))   ## the path should be for any CONUS nwm data

X_NWM = nc_NWM.coords['x']
Y_NWM = nc_NWM.coords['y']

# Calculate the distance between the center of grids from the location of the site

# indiceses based on the bottom left corner
distance = ((Y_NWM - bottom)**2 + (X_NWM - left)**2)**0.5
y1_index, x1_index = np.where(distance == distance.min())

# indiceses based on the top right corner
distance = ((Y_NWM - top)**2 + (X_NWM - right)**2)**0.5
y2_index, x2_index = np.where(distance == distance.min())

# print(x1_index, str(x2_index), y1_index, y2_index)
# Indices used for subsetting the AORC datasets
print("x1_index: {}, x2_index:{}, y1_index: {}, y2_index:{}".format(x1_index[0], x2_index[0], y1_index[0], y2_index[0]))

x1_index: 1122, x2_index:1136, y1_index: 2212, y2_index:2221


<div class="alert alert-block alert-success">
<b>  Subsetting the AWS forcing data using the the shapefile extent indices</b> 

</div>

In [13]:
## Create a directory to host the subsetted data
path = './AORC_AWS_Subset'
# Check whether the specified path exists or not
isExist = os.path.exists(path)
if not isExist:
# Create a new directory because it does not exist
   os.makedirs(path)

    
for forcing_file in os.listdir('./AORC_AWS'):
    subprocess.run(["ncks", './AORC_AWS'+'/'+forcing_file, "-d", "west_east,"+str(x1_index[0])+","+str(x2_index[0]), "-d", "south_north,"+str(y1_index[0])+","+str(y2_index[0]), "-O", './AORC_AWS_Subset/'+str(forcing_file)], capture_output=True)
    # tt=(["ncks", './AORC_AWS'+'/'+forcing_file, "-d", "west_east,"+str(x1_index[0])+","+str(x2_index[0]), "-d", "south_north,"+str(y1_index[0])+","+str(y2_index[0]), "-O", './AORC_AWS_Subset/'+str(forcing_file)], capture_output=True)
    # print(tt)
    # subprocess.run(tt)

<div class="alert alert-block alert-success">
<b>  Subsetting forcing data retrieved from Cheyenne using the shapefile extent indices</b> 

</div>

In [14]:
## Create a directory to host the subsetted data
path = './AORC_Cheyenne_Subset'
# Check whether the specified path exists or not
isExist = os.path.exists(path)
if not isExist:
# Create a new directory because it does not exist
   os.makedirs(path)
    
for forcing_file in os.listdir('./AORC_Cheyenne'):
    subprocess.run(["ncks", './AORC_Cheyenne'+'/'+forcing_file, "-d", "x,"+str(x1_index[0])+","+str(x2_index[0]), "-d", "y,"+str(y1_index[0])+","+str(y2_index[0]), "-O", './AORC_Cheyenne_Subset/'+str(forcing_file)], capture_output=True)

<div class="alert alert-block alert-success">
<b>  Check the size of the subset files</b> 

</div>

In [15]:
aws_subset_path='./AORC_AWS_Subset'
ch_subset_path='./AORC_Cheyenne_Subset'

for aws, ch in zip(sorted(os.listdir(aws_subset_path)), sorted(os.listdir(ch_subset_path))):
    subprocess.run(["du", "-h", aws_subset_path+"/"+str(aws)])
    subprocess.run(["du", "-h", ch_subset_path+"/"+str(ch)])

4.0K	./AORC_AWS_Subset/.ipynb_checkpoints
108K	./AORC_Cheyenne_Subset/201601010000.LDASIN_DOMAIN1
16K	./AORC_AWS_Subset/2016010100.LDASIN_DOMAIN1
108K	./AORC_Cheyenne_Subset/201601010100.LDASIN_DOMAIN1
16K	./AORC_AWS_Subset/2016010101.LDASIN_DOMAIN1
108K	./AORC_Cheyenne_Subset/201601010200.LDASIN_DOMAIN1


<div class="alert alert-block alert-success">
<b>  Merge all netCDF files into one file </b> 

</div>

In [16]:
## AORC from AWS
# Create a directory to host the merged dataset
aws_merge_path = './AORC_AWS_Subset_Merge'
# Check whether the specified path exists or not
isExist = os.path.exists(aws_merge_path)
if not isExist:
# Create a new directory because it does not exist
   os.makedirs(aws_merge_path)

# concatenate list of files into one file with relative time axis
subprocess.run(["cdo", "cat", './AORC_AWS_Subset/*', aws_merge_path+"/"+'AWS_Merged_File.nc'])

###########################################################################################
###########################################################################################
## AORC from Cheyenne
# Create a directory to host the merged dataset
ch_merge_path = './AORC_Cheyenne_Subset_Merge'
# Check whether the specified path exists or not
isExist = os.path.exists(ch_merge_path)
if not isExist:
# Create a new directory because it does not exist
   os.makedirs(ch_merge_path)

# concatenate list of files into one file with relative time axis
subprocess.run(["cdo", "cat", './AORC_Cheyenne_Subset/*', ch_merge_path+"/"+'Cheyenne_Merged_File.nc'])

Warning (cdf_set_gridtype): NetCDF attribute grid_type='latitude/longitude' unsupported!
Warning (cdf_set_zaxistype): NetCDF attribute level_type='ground or water surface' unsupported!
Warning (cdfCheckVars): Unsupported data type (char/string), skipped variable Times!

cdo    cat (Abort): Grid size of the input parameter LWDOWN do not match!

cdo    cat (Abort): Grid size of the input parameter LQFRAC do not match!


CompletedProcess(args=['cdo', 'cat', './AORC_Cheyenne_Subset/*', './AORC_Cheyenne_Subset_Merge/Cheyenne_Merged_File.nc'], returncode=1)

<div class="alert alert-block alert-success">
<b>The metadata for each subset of AORC data (AWS vs. Cheyenne)</b> 

</div>

In [17]:
## Metadata of each dataset

aws_merge_file_path = aws_merge_path + "/AWS_Merged_File.nc"   # path of the AWS merged netCDF file
ch_merge_file_path = ch_merge_path + "/Cheyenne_Merged_File.nc"  # path of the Cheyenne netCDF file          

meta_data_aws_merged = subprocess.run(["ncdump", "-h", aws_merge_file_path])
meta_data_ch_merged = subprocess.run(["ncdump", "-h", ch_merge_file_path])
print(meta_data_aws_merged)
print(meta_data_ch_merged)

netcdf AWS_Merged_File {
dimensions:
	valid_time = UNLIMITED ; // (3 currently)
	west_east = 43 ;
	south_north = 44 ;
variables:
	double valid_time(valid_time) ;
		valid_time:standard_name = "time" ;
		valid_time:units = "seconds since 1970-01-01 00:00:00" ;
		valid_time:calendar = "standard" ;
		valid_time:axis = "T" ;
	float LWDOWN(valid_time, south_north, west_east) ;
		LWDOWN:long_name = "Downward long-wave rad. flux" ;
		LWDOWN:units = "W m-2" ;
		LWDOWN:_FillValue = 9.999e+20f ;
		LWDOWN:missing_value = 9.999e+20f ;
		LWDOWN:remap = "remapped via ESMF_regrid_with_weights: Bilinear" ;
		LWDOWN:statistical_process_duration = "initial time to forecast time" ;
		LWDOWN:type_of_statistical_processing = "Accumulation" ;
		LWDOWN:center = "US National Weather Service - NCEP (WMC)" ;
		LWDOWN:production_status = "Operational products" ;
		LWDOWN:parameter_discipline_and_category = "Meteorological products, Long wave radiation" ;
		LWDOWN:parameter_template_discipline_category_number = 0,

<div class="alert alert-block alert-success">
<b>Push back the merged AORC datasets to the HydroShare resource</b> 

</div>

In this step, the merged AORC files from AWS and Cheyenne are added to the current HydroShare resource to set-up the THREDDS OpenDAP services.

1. Install the hstools for pushing back the mergered AORC files into the HydroShare resource

In [18]:
!pip install hstools

Defaulting to user installation because normal site-packages is not writeable
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 41.7/41.7 KB 2.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 133.4/133.4 KB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.8/58.8 KB 9.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 630.1/630.1 KB 23.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 125.6/125.6 KB 18.3 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
osmnx 1.1.2 requires Shapely<2.0,>=1.7, but you have shapely 2.0.1 which is incompatible.


2. List down the IDs of all HydroShare resources using the filter function.

In [19]:
!hs list -l -filter text="AORC"

Traceback (most recent call last):
  File "/home/jovyan/.local/python3-2022-06/bin/hs", line 84, in <module>
    args.func(args)
  File "/home/jovyan/.local/python3-2022-06/lib/python3.9/site-packages/hstools/funcs/ls.py", line 106, in main
    hs = hydroshare.hydroshare()
  File "/home/jovyan/.local/python3-2022-06/lib/python3.9/site-packages/hstools/hydroshare.py", line 62, in __init__
    raise Exception(f'Authentication failed using: {self.authfile}')
Exception: Authentication failed using: /home/jovyan/.hs_auth


3. We selected the ID of the current resource and we used the `describe` function to show the metadata.

In [20]:
!hs describe '0a1ad9f2f1284ae4af835c796d749acb'

Traceback (most recent call last):
  File "/home/jovyan/.local/python3-2022-06/bin/hs", line 84, in <module>
    args.func(args)
  File "/home/jovyan/.local/python3-2022-06/lib/python3.9/site-packages/hstools/funcs/describe.py", line 77, in main
    hs = hydroshare.hydroshare()
  File "/home/jovyan/.local/python3-2022-06/lib/python3.9/site-packages/hstools/hydroshare.py", line 62, in __init__
    raise Exception(f'Authentication failed using: {self.authfile}')
Exception: Authentication failed using: /home/jovyan/.hs_auth


4. Add the merged AORC data to the current HydroShare resource.

In [21]:
resource_id = '0a1ad9f2f1284ae4af835c796d749acb'
!hs add {resource_id} -f ./AORC_AWS_Subset_Merge/AWS_Merged_File.nc:AORC_AWS_Subset_Merge/AWS_Merged_File.nc
!hs add {resource_id} -f ./AORC_Cheyenne_Subset_Merge/Cheyenne_Merged_File.nc:Cheyenne_Subset_Merge/Cheyenne_Merged_File.nc

Traceback (most recent call last):
  File "/home/jovyan/.local/python3-2022-06/bin/hs", line 84, in <module>
    args.func(args)
  File "/home/jovyan/.local/python3-2022-06/lib/python3.9/site-packages/hstools/funcs/add.py", line 67, in main
    hs = hydroshare.hydroshare()
  File "/home/jovyan/.local/python3-2022-06/lib/python3.9/site-packages/hstools/hydroshare.py", line 62, in __init__
    raise Exception(f'Authentication failed using: {self.authfile}')
Exception: Authentication failed using: /home/jovyan/.hs_auth
Traceback (most recent call last):
  File "/home/jovyan/.local/python3-2022-06/bin/hs", line 84, in <module>
    args.func(args)
  File "/home/jovyan/.local/python3-2022-06/lib/python3.9/site-packages/hstools/funcs/add.py", line 67, in main
    hs = hydroshare.hydroshare()
  File "/home/jovyan/.local/python3-2022-06/lib/python3.9/site-packages/hstools/hydroshare.py", line 62, in __init__
    raise Exception(f'Authentication failed using: {self.authfile}')
Exception: Authent

## Summarizing the differences between the two AORC forcing data versions in a dataframe

In [22]:
# AORC variables
var = ["RAINRATE", "T2D", "Q2D", "U2D", "V2D", "PSFC", "SWDOWN", "LWDOWN"]

# Varibales full name
var_name = ["Total precipitation", "Temperature", "Specific humdity", "U-component of wind", "V-component of wind"
            , "Pressure", "Downward short-wave radiation flux", "Downward long-wave radiation flux"]

# List of variables units
var_units= ["mm s^-1", "K", "kg kg-1", "m s-1", "m s-1", "Pa", "W m-2", "W m-2" ]

## Create a dataframe to summarize the infromation
df= pd.DataFrame()
df["Variable"]= var_name
df["Units"] = var_units

for aws, ch in zip(sorted(os.listdir('./AORC_AWS_Subset')), sorted(os.listdir('./AORC_Cheyenne_Subset'))):
    ll=[]
    for v in var:
        aorc_aws="./AORC_AWS_Subset/"+str(aws)
        aorc_ch="./AORC_Cheyenne_Subset/"+str(ch)

        # AWS dataset subset
        aws_subset = xr.open_dataset(aorc_aws)[v]
        aws_subset_xr=xr.DataArray(aws_subset)
        aws_subset_arr=xr.DataArray.to_numpy(aws_subset_xr)
        # plt.boxplot(rain_aws_arr.flatten())

        # Cheyenne dataset subset
        ch_subset = xr.open_dataset(aorc_ch)[v]
        ch_subset_xr=xr.DataArray(ch_subset)
        ch_subset_arr=xr.DataArray.to_numpy(ch_subset_xr)
        # print(rain_ch_arr)

        # Calculate the difference between the two datasets from AWS and Cheyenne
        diff = aws_subset_arr - ch_subset_arr
        
        ll.append(np.mean(diff.flatten()))
    
    df[str(aws[0:10])]=ll
    
    ll=[]
df

/cvmfs/cybergis.illinois.edu/software/conda/cjw/python3-2022-06/lib/python3.9/site-packages/xarray/backends/plugins.py:110: RuntimeWarning: 'netcdf4' fails while guessing
  warnings.warn(f"{engine!r} fails while guessing", RuntimeWarning)
/cvmfs/cybergis.illinois.edu/software/conda/cjw/python3-2022-06/lib/python3.9/site-packages/xarray/backends/plugins.py:110: RuntimeWarning: 'h5netcdf' fails while guessing
  warnings.warn(f"{engine!r} fails while guessing", RuntimeWarning)
/cvmfs/cybergis.illinois.edu/software/conda/cjw/python3-2022-06/lib/python3.9/site-packages/xarray/backends/plugins.py:110: RuntimeWarning: 'scipy' fails while guessing
  warnings.warn(f"{engine!r} fails while guessing", RuntimeWarning)
/cvmfs/cybergis.illinois.edu/software/conda/cjw/python3-2022-06/lib/python3.9/site-packages/xarray/backends/plugins.py:119: RuntimeWarning: 'netcdf4' fails while guessing
  warnings.warn(f"{engine!r} fails while guessing", RuntimeWarning)
/cvmfs/cybergis.illinois.edu/software/conda/c

ValueError: did not find a match in any of xarray's currently installed IO backends ['netcdf4', 'h5netcdf', 'scipy', 'rasterio', 'zarr']. Consider explicitly selecting one of the installed engines via the ``engine`` parameter, or installing additional IO dependencies, see:
https://docs.xarray.dev/en/stable/getting-started-guide/installing.html
https://docs.xarray.dev/en/stable/user-guide/io.html